### **Training TFT model for Telsa stock dataset**

#### Installing required Libraries

In [ ]:
!pip install lightning pytorch_forecasting optuna keras

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 811.0/811.0 kB 44.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 181.9/181.9 kB 15.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 364.4/364.4 kB 15.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 233.5/233.5 kB 14.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 926.4/926.4 kB 46.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 815.2/815.2 kB 51.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.6/78.6 kB 7.8 MB/s eta 0:00:00


#### Imporing Required Libraries

In [ ]:
# General-purpose libraries
import copy
from pathlib import Path
import warnings
import numpy as np
import pandas as pd
import os
import torch

# PyTorch Lightning and Forecasting
import lightning.pytorch as pl
from lightning.pytorch.callbacks import EarlyStopping, LearningRateMonitor
from lightning.pytorch.loggers import TensorBoardLogger
from pytorch_forecasting import (
    Baseline,
    TemporalFusionTransformer,
    TimeSeriesDataSet,
)
from pytorch_forecasting.data import GroupNormalizer, NaNLabelEncoder
from pytorch_forecasting.metrics import MAE, SMAPE, PoissonLoss, QuantileLoss
from pytorch_forecasting.models.temporal_fusion_transformer.tuning import optimize_hyperparameters

# TensorFlow/Keras
from keras.models import Sequential
from keras.layers import LSTM, Dense, Dropout
from keras.optimizers import Adam
from tensorflow.keras.callbacks import EarlyStopping as ESLSTM

# Visualization libraries
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import plotly.express as px

# Sklearn for preprocessing and metrics
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_absolute_error, mean_squared_error

#### Load the preprocessed Tesla stock dataset with sentiment analysis of Reddit and news data from January 2018 to November 2024

### **Note:** Before running the cell below, ensure that tsla_data_with_sentiment_analysis_from_18_to_24.csv file from the `Stock_Web_UI` folder is uploaded to the session storage.

In [ ]:
tesla_fp = "/content/tsla_data_with_sentiment_analysis_from_18_to_24.csv"
# Load the dataset
tesla_df = pd.read_csv(tesla_fp)

In [ ]:
tesla_df

Date        Open        High         Low       Close   Adj Close  \
0     2018-01-02   20.799999   21.474001   20.733334   21.368668   21.368668   
1     2018-01-03   21.400000   21.683332   21.036667   21.150000   21.150000   
2     2018-01-04   20.858000   21.236668   20.378668   20.974667   20.974667   
3     2018-01-05   21.108000   21.149332   20.799999   21.105333   21.105333   
4     2018-01-08   21.066668   22.468000   21.033333   22.427334   22.427334   
...          ...         ...         ...         ...         ...         ...   
1735  2024-11-22  341.089996  361.529999  337.700012  352.559998  352.559998   
1736  2024-11-25  360.140015  361.929993  338.200012  338.589996  338.589996   
1737  2024-11-26  341.000000  346.959991  335.660004  338.230011  338.230011   
1738  2024-11-27  341.799988  342.549988  326.589996  332.890015  332.890015   
1739  2024-11-29  336.079987  345.450012  334.649994  345.160004  345.160004   

         Volume reddit_sentiment news_sentiment  
0      65283000          Neutral       Positive  
1      67822500         Positive        Neutral  
2     149194500         Positive       Positive  
3      68868000          Neutral       Positive  
4     147891000          Neutral       Positive  
...         ...              ...            ...  
1735   89140700         Positive       Positive  
1736   95890900         Positive       Positive  
1737   62295900         Positive       Positive  
1738   57896400          Neutral       Positive  
1739   37167600         Positive       Positive  

[1740 rows x 9 columns]

#### Data Preprocessing

In [ ]:
# Convert Date column
tesla_df['Date'] = pd.to_datetime(tesla_df['Date'])

# Set Date as the index
tesla_df.set_index('Date', inplace=True)

# Resample to daily frequency to include all business dates
tesla_df = tesla_df.resample('B').asfreq()

# Forward fill missing values for specified numerical columns
tesla_df[['Open', 'High', 'Low', 'Close', 'Adj Close', 'Volume', 'reddit_sentiment', 'news_sentiment']] = tesla_df[['Open', 'High', 'Low', 'Close',
                                    'Adj Close', 'Volume', 'reddit_sentiment', 'news_sentiment']].ffill()

tesla_df.reset_index(inplace=True)

In [ ]:
tesla_df = tesla_df.merge(
    tesla_df[['Date']].drop_duplicates(ignore_index=True).rename_axis('time_idx').reset_index(),
    on='Date',
    how='left'
)

### Define the dataset for the TFT model

In [ ]:
# Define the dataset for the TFT model
max_prediction_length = 30
min_encoder_length = 0
max_encoder_length = 180
tesla_df['group_id'] = 0  # Assigning a constant group
# Define the TimeSeriesDataSet object
training_cutoff = tesla_df['time_idx'].max() - max_prediction_length

#### Create training set

In [ ]:
# Create training set
training = TimeSeriesDataSet(
    tesla_df[lambda x: x.time_idx <= training_cutoff],
    time_idx="time_idx",
    target="Close", # target variable
    group_ids=["group_id"], # static covariates
    max_encoder_length=max_encoder_length, # maximum size of lookup window
    min_encoder_length=max_encoder_length//2,
    max_prediction_length=max_prediction_length, # maximum size of horizon window
    min_prediction_length=max_prediction_length,
    time_varying_known_categoricals=[],
    time_varying_known_reals=['Open', 'Volume'],
    time_varying_unknown_categoricals=['reddit_sentiment', 'news_sentiment'],
    time_varying_unknown_reals=['Close'],
    target_normalizer=GroupNormalizer(
        groups=["group_id"], transformation="softplus"
    ),  # use softplus transformation and normalize by group
    lags={'Close': [7,15,30,45,60,90]}, # add lagged values of target variable
    add_relative_time_idx=True,
    add_target_scales=True,
    add_encoder_length=True,
    categorical_encoders={
          # Properly handle unknown categories
        "reddit_sentiment": NaNLabelEncoder(),
        "news_sentiment": NaNLabelEncoder()
    }
)

In [ ]:
# create validation set
validation = TimeSeriesDataSet.from_dataset(training, tesla_df, predict=True, stop_randomization=True)

# create dataloaders for model
batch_size = 128
train_dataloader = training.to_dataloader(train=True, batch_size=batch_size, num_workers=8)
val_dataloader = validation.to_dataloader(train=False, batch_size=batch_size * 10, num_workers=8)

In [ ]:
# calculate baseline mean absolute error
baseline_predictions = Baseline().predict(val_dataloader, return_y=True)
MAE()(baseline_predictions.output, baseline_predictions.y)

<ipython-input-11-18f9a4de925b>:2: UserWarning: In pytorch-forecasting models, on versions 1.1.X, the default optimizer defaults to 'adam', if pytorch_optimizer is not installed, otherwise it defaults to 'ranger' from pytorch_optimizer. From version 1.2.0, the default optimizer will be 'adam' regardless of whether pytorch_optimizer is installed, in order to minimize the number of dependencies in default parameter settings. Users who wish to ensure their code continues using 'ranger' as optimizer should ensure that pytorch_optimizer is installed, and set the optimizer parameter explicitly to 'ranger'.
  baseline_predictions = Baseline().predict(val_dataloader, return_y=True)
/usr/local/lib/python3.10/dist-packages/lightning/pytorch/utilities/parsing.py:208: Attribute 'loss' is an instance of `nn.Module` and is already saved during checkpointing. It is recommended to ignore them using `self.save_hyperparameters(ignore=['loss'])`.
/usr/local/lib/python3.10/dist-packages/lightning/pytorch/

tensor(76.9703, device='cuda:0')

### Definint the function to tune hyperparameters from Optuna

In [ ]:
import optuna
import lightning.pytorch as pl
from lightning.pytorch.callbacks import EarlyStopping, LearningRateMonitor
from pytorch_forecasting import TemporalFusionTransformer
from pytorch_forecasting.metrics import QuantileLoss, MAE
from pytorch_forecasting.data import GroupNormalizer

# Define the objective function for Optuna to tune hyperparameters
def objective(trial):
    # Suggest hyperparameters to tune
    learning_rate = trial.suggest_loguniform('learning_rate', 1e-5, 1e-2)
    hidden_size = trial.suggest_int('hidden_size', 8, 64)
    attention_head_size = trial.suggest_int('attention_head_size', 1, 4)
    dropout = trial.suggest_uniform('dropout', 0.1, 0.5)

    # Define the TFT model with suggested hyperparameters
    tft = TemporalFusionTransformer.from_dataset(
        training,
        learning_rate=learning_rate,
        hidden_size=hidden_size,
        attention_head_size=attention_head_size,
        dropout=dropout,
        hidden_continuous_size=hidden_size // 2,  # Optional, adjusts continuous features
        loss=QuantileLoss(),
        optimizer="Adam"
    )

    # Set up the PyTorch Lightning Trainer with early stopping
    trainer = pl.Trainer(
        max_epochs=10,
        gradient_clip_val=0.1,
        callbacks=[EarlyStopping(monitor="val_loss", patience=3)],
        accelerator="gpu"
    )

    # Train the model
    trainer.fit(tft, train_dataloader, val_dataloader)

    # Get predictions on the validation set
    val_predictions = tft.predict(val_dataloader, return_y=True)

    # Calculate validation MAE as the optimization target
    val_mae = MAE()(val_predictions.output, val_predictions.y).item()
    return val_mae

# Run the hyperparameter optimization
study = optuna.create_study(direction="minimize")
study.optimize(objective, n_trials=30)  # Adjust n_trials for more exhaustive search if needed

# Print the best parameters found by Optuna
best_params = study.best_params
print("Best hyperparameters:", best_params)

[I 2024-12-02 16:37:39,888] A new study created in memory with name: no-name-399412ba-e84c-4911-b0b7-2cdc31946a91
<ipython-input-13-978a4dae183e>:11: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  learning_rate = trial.suggest_loguniform('learning_rate', 1e-5, 1e-2)
<ipython-input-13-978a4dae183e>:14: FutureWarning: suggest_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float instead.
  dropout = trial.suggest_uniform('dropout', 0.1, 0.5)
INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/lightning/pytorch/loops/fit_loop.py:298: The number of training batches (12) is smaller than the logging interval Trainer(log_every_n_steps=50). Set a lower value for log_every_n_steps if you want to see logs for the training epoch.


Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO: `Trainer.fit` stopped: `max_epochs=10` reached.
INFO:lightning.pytorch.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=10` reached.
INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
[I 2024-12-02 16:57:39,009] Trial 29 finished with value: 7.676491737365723 and parameters: {'learning_rate': 0.0007693367817925835, 'hidden_size': 24, 'attention_head_size': 3, 'dropout': 0.19608882013889972}. Best is trial 29 with value: 7.676491737365723.


Best hyperparameters: {'learning_rate': 0.0007693367817925835, 'hidden_size': 24, 'attention_head_size': 3, 'dropout': 0.19608882013889972}


In [ ]:
best_params

{'learning_rate': 0.0007693367817925835,
 'hidden_size': 24,
 'attention_head_size': 3,
 'dropout': 0.19608882013889972}

In [ ]:
# configure network and trainer
pl.seed_everything(42)
trainer = pl.Trainer(
    accelerator="gpu",
    gradient_clip_val=0.1,
)

tft = TemporalFusionTransformer.from_dataset(
    training,
    learning_rate=0.0007693367817925835,
    hidden_size=24,
    attention_head_size=3,
    dropout=0.19608882013889972,
    hidden_continuous_size=24,
    loss=QuantileLoss(),
    optimizer="Adam"
)
print(f"Number of parameters in network: {tft.size()/1e3:.1f}k")

INFO: Seed set to 42
INFO:lightning.fabric.utilities.seed:Seed set to 42
INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs


Number of parameters in network: 85.7k


#### Training the TFT model

In [ ]:
# Configure EarlyStopping with patience and monitoring validation loss
early_stop_callback = EarlyStopping(
    monitor="val_loss",
    min_delta=1e-4,
    patience=15,
    verbose=True,
    mode="min",
    stopping_threshold=None,
    check_finite=True
)

lr_logger = LearningRateMonitor()  # Log the learning rate
logger = TensorBoardLogger("lightning_logs")  # Log results to TensorBoard

trainer = pl.Trainer(
    accelerator="gpu",  # Set to "gpu" if you have a GPU available
    enable_model_summary=True,
    gradient_clip_val=0.1,
    limit_train_batches=1.0,  # Use the entire dataset for training
    callbacks=[lr_logger, early_stop_callback],
    logger=logger,
    check_val_every_n_epoch=1,  # Validate every epoch
)

# Define the Temporal Fusion Transformer
tft = TemporalFusionTransformer.from_dataset(
    training,
    learning_rate=0.0007693367817925835,
    hidden_size=24,
    attention_head_size=3,
    dropout=0.19608882013889972,
    hidden_continuous_size=24,
    loss=QuantileLoss(),
    log_interval=10,
    optimizer="Adam",
    reduce_on_plateau_patience=4,
)

INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: `Trainer(limit_train_batches=1.0)` was configured so 100% of the batches per epoch will be used..
INFO:lightning.pytorch.utilities.rank_zero:`Trainer(limit_train_batches=1.0)` was configured so 100% of the batches per epoch will be used..


In [ ]:
# Train the model
trainer.fit(tft, train_dataloader, val_dataloader)

/usr/local/lib/python3.10/dist-packages/lightning/pytorch/loops/utilities.py:72: `max_epochs` was not set. Setting it to 1000 epochs. To train without an epoch limit, set `max_epochs=-1`.
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO: 
   | Name                               | Type                            | Params | Mode 
------------------------------------------------------------------------------------------------
0  | loss                               | QuantileLoss                    | 0      | train
1  | logging_metrics                    | ModuleList                      | 0      | train
2  | input_embeddings                   | MultiEmbedding                  | 11     | train
3  | prescalers                         | ModuleDict                      | 624    | train
4  | static_variable_selection          | VariableSelectionNetwork        | 7.8 K  | train
5  | encoder_variable_selection

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/lightning/pytorch/loops/fit_loop.py:298: The number of training batches (12) is smaller than the logging interval Trainer(log_every_n_steps=50). Set a lower value for log_every_n_steps if you want to see logs for the training epoch.


Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO: Monitored metric val_loss did not improve in the last 15 records. Best score: 4.263. Signaling Trainer to stop.
INFO:lightning.pytorch.callbacks.early_stopping:Monitored metric val_loss did not improve in the last 15 records. Best score: 4.263. Signaling Trainer to stop.


In [ ]:
# calcualte mean absolute error on validation set
predictions = tft.predict(val_dataloader, return_y=True, trainer_kwargs=dict(accelerator="cpu"))
MAE()(predictions.output, predictions.y)

INFO: GPU available: True (cuda), used: False
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: False
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
/usr/local/lib/python3.10/dist-packages/lightning/pytorch/trainer/setup.py:177: GPU available but not used. You can set it by doing `Trainer(accelerator='gpu')`.


tensor(8.5190)

#### Visualizations

In [ ]:
# Prepare Data for Visualization
actuals = predictions.y[0].detach().numpy().flatten()
preds = predictions.output.detach().numpy().flatten()

validation_dates = tesla_df['Date'][-len(actuals):].values

# Calculate Mean Absolute Error (MAE)
mae = MAE()(predictions.output, predictions.y[0])
print(f"Mean Absolute Error: {mae.item()}")

# Create Plotly figure
fig = go.Figure()


fig.add_trace(go.Scatter(
    x=validation_dates,
    y=actuals,
    mode='lines',
    name='Actual Values',
    line=dict(color='blue')
))


fig.add_trace(go.Scatter(
    x=validation_dates,
    y=preds,
    mode='lines',
    name='Predicted Values',
    line=dict(color='green')
))

fig.update_layout(
    title="Predictions vs Actuals on Validation Set",
    xaxis_title="Date",
    yaxis_title="Stock Price",
    legend_title="Legend",
    template="plotly_dark"
)

# Show the plot
fig.show()

Mean Absolute Error: 8.519037246704102


In [ ]:
dates = tesla_df['Date'][-len(actuals):].values

# Step 1: Create a DataFrame for Backtesting
trading_df = pd.DataFrame({
    'Date': dates,
    'Actual': actuals,
    'Predicted': preds
})
trading_df.set_index('Date', inplace=True)

# Calculate daily returns based on actual prices
trading_df['Daily Return'] = trading_df['Actual'].pct_change()

# Step 2: Generate Buy/Sell Signals Based on Predicted Prices
# Signal: 1 (Buy) if predicted price is higher than the previous prediction, -1 (Sell) otherwise
trading_df['Signal'] = np.where(trading_df['Predicted'].diff() > 0, 1, -1)

# Calculate strategy returns by shifting the signal by 1 to avoid lookahead bias
trading_df['Strategy Return'] = trading_df['Signal'].shift(1) * trading_df['Daily Return']

# Step 3: Calculate Cumulative Returns for Strategy and Benchmark
# Cumulative return for the TFT-based strategy
trading_df['Cumulative Strategy Return'] = (1 + trading_df['Strategy Return']).cumprod() - 1
# Cumulative return for a simple buy-and-hold strategy
trading_df['Cumulative Buy and Hold Return'] = (1 + trading_df['Daily Return']).cumprod() - 1

# Print final cumulative returns for both strategies
print(f"Final Strategy Return: {trading_df['Cumulative Strategy Return'].iloc[-1] * 100:.2f}%")
print(f"Final Buy and Hold Return: {trading_df['Cumulative Buy and Hold Return'].iloc[-1] * 100:.2f}%")

# Step 4: Plot Strategy vs. Buy-and-Hold Performance
fig = go.Figure()

# Cumulative strategy return plot
fig.add_trace(go.Scatter(
    x=trading_df.index,
    y=trading_df['Cumulative Strategy Return'],
    mode='lines',
    name='Cumulative Strategy Return',
    line=dict(color='blue')
))

# Cumulative buy-and-hold return plot
fig.add_trace(go.Scatter(
    x=trading_df.index,
    y=trading_df['Cumulative Buy and Hold Return'],
    mode='lines',
    name='Cumulative Buy and Hold Return',
    line=dict(color='green')
))

# Update layout for readability
fig.update_layout(
    title="TFT-Based Trading Strategy vs Buy-and-Hold",
    xaxis_title="Date",
    yaxis_title="Cumulative Return",
    template="plotly_dark"
)

fig.show()

Final Strategy Return: 89.51%
Final Buy and Hold Return: 57.72%


In [ ]:
# Set initial investment amount
initial_investment = 10000

# Calculate total earnings for the last 15 days
last_15_days = trading_df['Cumulative Strategy Return'].iloc[-15:]
final_return = last_15_days.iloc[-1]  # Get the last cumulative return

# Calculate final balance and earnings
final_balance = initial_investment * (1 + final_return)
earnings = final_balance - initial_investment

print(f"Initial Investment: ${initial_investment:,.2f}")
print(f"Final Balance after 15 days: ${final_balance:,.2f}")
print(f"Earnings over 15 days: ${earnings:,.2f}")

Initial Investment: $10,000.00
Final Balance after 15 days: $18,951.38
Earnings over 15 days: $8,951.38


#### Checking feature importance and MAE, RMSE, AND r2 Score for TFT Model

In [ ]:
# Calculate errors
errors = np.abs(actuals - preds)
fig = px.histogram(errors, nbins=50, title="Distribution of Absolute Errors", template="plotly_dark")
fig.update_layout(
    xaxis_title="Absolute Error",
    yaxis_title="Frequency"
)
fig.show()

# Print MAE and MSE
print(f"Mean Absolute Error: {mean_absolute_error(actuals, preds)}")
print(f"Mean Squared Error: {mean_squared_error(actuals, preds)}")

Mean Absolute Error: 8.519037246704102
Mean Squared Error: 117.52493286132812


In [ ]:
from sklearn.metrics import root_mean_squared_error, r2_score

# Calculate RMSE and R²
rmse = root_mean_squared_error(actuals, preds)
r2 = r2_score(actuals, preds)

print(f"RMSE: {rmse}, R²: {r2}")

RMSE: 10.84089183807373, R²: 0.9420342445373535


In [ ]:
# Using `mode="raw"` to get all outputs for interpretation
raw_predictions = tft.predict(val_dataloader, mode="raw", return_x=True)

# Unpack only what is necessary from raw_predictions
pred = raw_predictions[0]  # This contains the prediction values
x = raw_predictions[1]  # This contains input data used for interpretation

INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


In [ ]:
interpretation = tft.interpret_output(pred, reduction="mean")

In [ ]:
import pandas as pd
import plotly.express as px

# Extract feature importance from `static_variables`, `encoder_variables`, and `decoder_variables`
# Replace with actual feature names if needed
features = {
    "Static Features": interpretation["static_variables"].cpu().numpy(),
    "Encoder Features": interpretation["encoder_variables"].cpu().numpy(),
    "Decoder Features": interpretation["decoder_variables"].cpu().numpy(),
}

# Flatten the data for plotting
feature_names = []
feature_importance = []

for category, values in features.items():
    for i, value in enumerate(values):
        feature_names.append(f"{category}_{i+1}")  # or replace with actual feature names if available
        feature_importance.append(value)

# Create DataFrame for feature importance
importance_df = pd.DataFrame({
    "Feature": feature_names,
    "Importance": feature_importance
}).sort_values(by="Importance", ascending=False)

# Plot Feature Importance with Plotly
fig = px.bar(importance_df, x="Importance", y="Feature", orientation='h', title="Feature Importance", template="plotly_dark")
fig.update_layout(xaxis_title="Importance", yaxis_title="Feature")
fig.show()

In [ ]:
# Extract temporal attention values from the interpretation output
attention_weights = interpretation["attention"].cpu().numpy()  # Convert to numpy for easier handling
time_steps = list(range(len(attention_weights)))  # Generate time steps for x-axis

# Create the Plotly figure
fig = go.Figure()

# Plot attention weights as a single line
fig.add_trace(go.Scatter(
    x=time_steps,
    y=attention_weights,
    mode='lines',
    name="Attention Weight",
    line=dict(color='cyan')
))

# Update the layout for clarity
fig.update_layout(
    title="Temporal Attention Weights",
    xaxis_title="Time Steps",
    yaxis_title="Attention Weight",
    template="plotly_dark"
)

# Show the plot
fig.show()

### Downloading the Trained TFT Model of Tesla stcok

In [ ]:
import torch
torch.save(tft.state_dict(), 'tesla_trained_tft_model.pth')
from google.colab import files
# Download the file
files.download('tesla_trained_tft_model.pth')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

#### LSTM model

In [ ]:
# Load the dataset
tesla_data = pd.read_csv(tesla_fp)

# Parse dates and set the index
tesla_data['Date'] = pd.to_datetime(tesla_data['Date'])
tesla_data.set_index('Date', inplace=True)

# Use only the 'Close' column for prediction
close_prices = tesla_data[['Close']].values

# Scale the data to be between 0 and 1
scaler = MinMaxScaler(feature_range=(0, 1))
scaled_data = scaler.fit_transform(close_prices)

# Prepare the dataset for the LSTM
sequence_length = 90  # Using 90 days of historical data to predict the next day
X = []
y = []

for i in range(sequence_length, len(scaled_data)):
    X.append(scaled_data[i-sequence_length:i, 0])
    y.append(scaled_data[i, 0])

X, y = np.array(X), np.array(y)
X = np.reshape(X, (X.shape[0], X.shape[1], 1))  # Reshape for LSTM [samples, time steps, features]

# Split the data into training and testing sets
train_size = int(len(X) * 0.8)
X_train, X_test = X[:train_size], X[train_size:]
y_train, y_test = y[:train_size], y[train_size:]

# Build the LSTM model
model = Sequential()
model.add(LSTM(units=100, return_sequences=True, input_shape=(X_train.shape[1], 1)))
model.add(Dropout(0.25))
model.add(LSTM(units=50, return_sequences=False))
model.add(Dropout(0.20))
model.add(Dense(units=25))
model.add(Dense(units=1))

# Compile the model
model.compile(optimizer=Adam(learning_rate=0.01), loss='mean_squared_error')

# Set up EarlyStopping callback
early_stopping = ESLSTM(
    monitor='val_loss',   # Monitor the validation loss
    patience=10,
    verbose=1,
    restore_best_weights=True
)

# Train the model with early stopping
history = model.fit(
    X_train, y_train,
    epochs=100,                # Set a high number of epochs
    batch_size=32,
    validation_data=(X_test, y_test),
    callbacks=[early_stopping], # Add the early stopping callback
    verbose=1
)

# Make predictions
lstm_predictions = model.predict(X_test)
predictions = scaler.inverse_transform(lstm_predictions)  # Invert scaling to get original values

# Invert scaling for y_test as well
y_test_scaled = scaler.inverse_transform(y_test.reshape(-1, 1))

Epoch 1/100


/usr/local/lib/python3.10/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning:

Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.



42/42 ━━━━━━━━━━━━━━━━━━━━ 3s 17ms/step - loss: 0.1543 - val_loss: 0.0033
Epoch 2/100
42/42 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 0.0049 - val_loss: 0.0017
Epoch 3/100
42/42 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 0.0024 - val_loss: 0.0016
Epoch 4/100
42/42 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 0.0019 - val_loss: 0.0015
Epoch 5/100
42/42 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 0.0020 - val_loss: 0.0013
Epoch 6/100
42/42 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 0.0019 - val_loss: 0.0014
Epoch 7/100
42/42 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 0.0019 - val_loss: 0.0023
Epoch 8/100
42/42 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 0.0021 - val_loss: 0.0011
Epoch 9/100
42/42 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 0.0015 - val_loss: 0.0017
Epoch 10/100
42/42 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 0.0020 - val_loss: 0.0012
Epoch 11/100
42/42 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - loss: 0.0016 - val_loss: 0.0011
Epoch 12/100
42/42 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - loss: 0.0

In [ ]:
# Calculate the Mean Absolute Error (MAE) between the actual and predicted values
mae_value = mean_absolute_error(y_test_scaled, lstm_predictions)
print(f"Mean Absolute Error (MAE): {mae_value}")

# Calculate the Mean Absolute Error (MAE) for the last 30 days
days = 30
mae_last_n_days = mean_absolute_error(y_test_scaled[-days:], predictions[-days:])
print(f"Mean Absolute Error (MAE) for the Last {days} Days: {mae_last_n_days}")

# Prepare the plot with Plotly for the last 30 days
fig = go.Figure()

fig.add_trace(go.Scatter(x=tesla_data.index[-len(y_test):][-days:], y=y_test_scaled.flatten()[-days:], mode='lines', name='Actual Prices'))
fig.add_trace(go.Scatter(x=tesla_data.index[-len(y_test):][-days:], y=predictions.flatten()[-days:], mode='lines', name='Predicted Prices'))

# Update the layout
fig.update_layout(
    title="Last 30 Days Stock Price Prediction",
    xaxis_title="Date",
    yaxis_title="Stock Price",
    legend_title="Legend",
    template="plotly"
)

# Show the plot
fig.show()

Mean Absolute Error (MAE): 221.57285258462935
Mean Absolute Error (MAE) for the Last 30 Days: 12.1790044148763


In [ ]:
from sklearn.metrics import root_mean_squared_error, r2_score

# Calculate RMSE and R²
rmse = root_mean_squared_error(y_test_scaled, lstm_predictions)
r2 = r2_score(y_test_scaled, lstm_predictions)

print(f"RMSE: {rmse}, R²: {r2}")

RMSE: 225.1864501653548, R²: -30.264928583919023
